# Coursera IBM Data Science Capstone Project - Week 3

This notebook will be used to do the Coursera IBM Capstone Project!

# Disclaimer: Folium maps do NOT render inside GitHub.com visualization. Please evaluate locally in your machine if you want to see the maps!!

# Part 1: Segmenting and Clustering Neighborhoods in Toronto

## Libraries Import

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


## Data Preparation

In [2]:
import pandas as pd
import numpy as np

In [3]:
print("Hello Capstone Project Course!")

Hello Capstone Project Course!


In [4]:
df = pd.read_html("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M")
df = df[0]

In [5]:
df

Postal Code           Borough  \
0           M1A      Not assigned   
1           M2A      Not assigned   
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
5           M6A        North York   
6           M7A  Downtown Toronto   
7           M8A      Not assigned   
8           M9A         Etobicoke   
9           M1B       Scarborough   
10          M2B      Not assigned   
11          M3B        North York   
12          M4B         East York   
13          M5B  Downtown Toronto   
14          M6B        North York   
15          M7B      Not assigned   
16          M8B      Not assigned   
17          M9B         Etobicoke   
18          M1C       Scarborough   
19          M2C      Not assigned   
20          M3C        North York   
21          M4C         East York   
22          M5C  Downtown Toronto   
23          M6C              York   
24          M7C      Not assigned   
25          M8C      Not assigned   
26          M9C         Etobicoke   
27          M1E       Scarborough   
28          M2E      Not assigned   
29          M3E      Not assigned   
30          M4E      East Toronto   
31          M5E  Downtown Toronto   
32          M6E              York   
33          M7E      Not assigned   
34          M8E      Not assigned   
35          M9E      Not assigned   
36          M1G       Scarborough   
37          M2G      Not assigned   
38          M3G      Not assigned   
39          M4G         East York   
40          M5G  Downtown Toronto   
41          M6G  Downtown Toronto   
42          M7G      Not assigned   
43          M8G      Not assigned   
44          M9G      Not assigned   
45          M1H       Scarborough   
46          M2H        North York   
47          M3H        North York   
48          M4H         East York   
49          M5H  Downtown Toronto   
50          M6H      West Toronto   
51          M7H      Not assigned   
52          M8H      Not assigned   
53          M9H      Not assigned   
54          M1J       Scarborough   
55          M2J        North York   
56          M3J        North York   
57          M4J         East York   
58          M5J  Downtown Toronto   
59          M6J      West Toronto   
60          M7J      Not assigned   
61          M8J      Not assigned   
62          M9J      Not assigned   
63          M1K       Scarborough   
64          M2K        North York   
65          M3K        North York   
66          M4K      East Toronto   
67          M5K  Downtown Toronto   
68          M6K      West Toronto   
69          M7K      Not assigned   
70          M8K      Not assigned   
71          M9K      Not assigned   
72          M1L       Scarborough   
73          M2L        North York   
74          M3L        North York   
75          M4L      East Toronto   
76          M5L  Downtown Toronto   
77          M6L        North York   
78          M7L      Not assigned   
79          M8L      Not assigned   
80          M9L        North York   
81          M1M       Scarborough   
82          M2M        North York   
83          M3M        North York   
84          M4M      East Toronto   
85          M5M        North York   
86          M6M              York   
87          M7M      Not assigned   
88          M8M      Not assigned   
89          M9M        North York   
90          M1N       Scarborough   
91          M2N        North York   
92          M3N        North York   
93          M4N   Central Toronto   
94          M5N   Central Toronto   
95          M6N              York   
96          M7N      Not assigned   
97          M8N      Not assigned   
98          M9N              York   
99          M1P       Scarborough   
100         M2P        North York   
101         M3P      Not assigned   
102         M4P   Central Toronto   
103         M5P   Central Toronto   
104         M6P      West Toronto   
105         M7P      Not assigned   
106         M8P      Not assigned   
107     

In [6]:
df.describe()

Postal Code       Borough Neighbourhood
count          180           180           180
unique         180            11           100
top            M2G  Not assigned  Not assigned
freq             1            77            77

In [7]:
df = df[df.Borough != 'Not assigned']

In [8]:
df.describe()

Postal Code     Borough Neighbourhood
count          103         103           103
unique         103          10            99
top            M2K  North York     Downsview
freq             1          24             4

In [9]:
#df.columns = [c.replace(' ', '_') for c in df.columns]
#df.Postal_Code
df.columns = [c.replace('Neighbourhood', 'Neighborhood') for c in df.columns]

In [10]:
df[df.Neighborhood == 'Not assigned']

Empty DataFrame
Columns: [Postal Code, Borough, Neighborhood]
Index: []

In [11]:
df.groupby(by='Postal Code', axis=0).head()

Postal Code           Borough  \
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
5           M6A        North York   
6           M7A  Downtown Toronto   
8           M9A         Etobicoke   
9           M1B       Scarborough   
11          M3B        North York   
12          M4B         East York   
13          M5B  Downtown Toronto   
14          M6B        North York   
17          M9B         Etobicoke   
18          M1C       Scarborough   
20          M3C        North York   
21          M4C         East York   
22          M5C  Downtown Toronto   
23          M6C              York   
26          M9C         Etobicoke   
27          M1E       Scarborough   
30          M4E      East Toronto   
31          M5E  Downtown Toronto   
32          M6E              York   
36          M1G       Scarborough   
39          M4G         East York   
40          M5G  Downtown Toronto   
41          M6G  Downtown Toronto   
45          M1H       Scarborough   
46          M2H        North York   
47          M3H        North York   
48          M4H         East York   
49          M5H  Downtown Toronto   
50          M6H      West Toronto   
54          M1J       Scarborough   
55          M2J        North York   
56          M3J        North York   
57          M4J         East York   
58          M5J  Downtown Toronto   
59          M6J      West Toronto   
63          M1K       Scarborough   
64          M2K        North York   
65          M3K        North York   
66          M4K      East Toronto   
67          M5K  Downtown Toronto   
68          M6K      West Toronto   
72          M1L       Scarborough   
73          M2L        North York   
74          M3L        North York   
75          M4L      East Toronto   
76          M5L  Downtown Toronto   
77          M6L        North York   
80          M9L        North York   
81          M1M       Scarborough   
82          M2M        North York   
83          M3M        North York   
84          M4M      East Toronto   
85          M5M        North York   
86          M6M              York   
89          M9M        North York   
90          M1N       Scarborough   
91          M2N        North York   
92          M3N        North York   
93          M4N   Central Toronto   
94          M5N   Central Toronto   
95          M6N              York   
98          M9N              York   
99          M1P       Scarborough   
100         M2P        North York   
102         M4P   Central Toronto   
103         M5P   Central Toronto   
104         M6P      West Toronto   
107         M9P         Etobicoke   
108         M1R       Scarborough   
109         M2R        North York   
111         M4R   Central Toronto   
112         M5R   Central Toronto   
113         M6R      West Toronto   
114         M7R       Mississauga   
116         M9R         Etobicoke   
117         M1S       Scarborough   
120         M4S   Central Toronto   
121         M5S  Downtown Toronto   
122         M6S      West Toronto   
126         M1T       Scarborough   
129         M4T   Central Toronto   
130         M5T  Downtown Toronto   
135         M1V       Scarborough   
138         M4V   Central Toronto   
139         M5V  Downtown Toronto   
142         M8V         Etobicoke   
143         M9V         Etobicoke   
144         M1W       Scarborough   
147         M4W  Downtown Toronto   
148         M5W  Downtown Toronto   
151         M8W         Etobicoke   
152         M9W         Etobicoke   
153         M1X       Scarborough   
156         M4X  Downtown Toronto   
157         M5X  Downtown Toronto   
160         M8X         Etobicoke   
165         M4Y  Downtown Toronto   
168         M7Y      East Toronto   
169         M8Y         Etobicoke   
178         M8Z         Etobicoke   

                                          Neighborhood  
2                                            Parkwoods  
3                                     Vic

In [12]:
df.shape

(103, 3)

### Let's pick only the rows that have the string 'Toronto' in the Borough column.

In [13]:
df_toronto = df[df['Borough'].str.contains("Toronto")]

In [14]:
postal_codes = list(df_toronto['Postal Code'].values)
borough = list(df_toronto['Borough'].values)

#### Geocoder cell doesn't work, importing coordinates via csv file (Geocoder cell below).

import geocoder # import geocoder
from time import sleep

#initialize your variable to None
lat_lng_coords = None
latlng_list = []

#loop until you get the coordinates
for postal_code in postal_codes:
    sleep(1)
    print(postal_code)
    while(lat_lng_coords is None):
        g = geocoder.google('{}, Toronto, Ontario'.format(postal_code))
        lat_lng_coords = g.latlng
    latlng_list.append(lat_lng_coords)
    print(lat_lng_coords)
    #latitude = lat_lng_coords[0]
    #longitude = lat_lng_coords[1]
    lat_lng_coords = None
print(latlng_list)

In [15]:
df_lat = pd.read_csv("Geospatial_Coordinates.csv")
df_lat.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [16]:
neighborhoods = pd.merge(df_lat,df_toronto,on='Postal Code')

In [17]:
neighborhoods.head()

Postal Code   Latitude  Longitude          Borough  \
0         M4E  43.676357 -79.293031     East Toronto   
1         M4K  43.679557 -79.352188     East Toronto   
2         M4L  43.668999 -79.315572     East Toronto   
3         M4M  43.659526 -79.340923     East Toronto   
4         M4N  43.728020 -79.388790  Central Toronto   

                     Neighborhood  
0                     The Beaches  
1    The Danforth West, Riverdale  
2  India Bazaar, The Beaches West  
3                 Studio District  
4                   Lawrence Park

## Toronto City Coordinates Creation

In [18]:
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto City are 43.6534817, -79.3839347.


## Map Creation

In [19]:
# create map of New York using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [20]:
def address_to_coordinates(address='Toronto, Ontario'):

    geolocator = Nominatim(user_agent="ny_explorer")
    location = geolocator.geocode(address)
    latitude = location.latitude
    longitude = location.longitude
    print('The geograpical coordinate of Toronto City are {}, {}.'.format(latitude, longitude))
    return [latitude, longitude]

def map_creator(dataframe, latitude=43.6534817, longitude=-79.3839347, state='both'):
    
    map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)
    if (state == 'both'):
        # add markers to map
        for lat, lng, neighborhood in zip(dataframe['Neighborhood Latitude'], dataframe['Neighborhood Longitude'], dataframe['Neighborhood']):
            label = '{}'.format(neighborhood)
            label = folium.Popup(label, parse_html=True)
            folium.CircleMarker(
                [lat, lng],
                radius=5,
                popup=label,
                color='blue',
                fill=True,
                fill_color='#3186cc',
                fill_opacity=0.7,
                parse_html=False).add_to(map_toronto)

        for lat, lng, neighborhood in zip(dataframe['Venue Latitude'], dataframe['Venue Longitude'], dataframe['Neighborhood']):
            label = '{}'.format(neighborhood)
            label = folium.Popup(label, parse_html=True)
            folium.CircleMarker(
                [lat, lng],
                radius=5,
                popup=label,
                color='green',
                fill=True,
                fill_color='#3186cc',
                fill_opacity=0.6,
                parse_html=False).add_to(map_toronto)
            
    return map_toronto

## Foursquare API Setup

In [21]:
CLIENT_ID = 'ESREBURGZAQYDGGE5MW2KQ4KIUTFICDE5ZG2QGDW2OWZ1XMI' # your Foursquare ID
CLIENT_SECRET = 'QISVXASEFWCY1RSEOLCLMLIC33VDEK3TRKKRAD2H2SQPK4OU' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: ESREBURGZAQYDGGE5MW2KQ4KIUTFICDE5ZG2QGDW2OWZ1XMI
CLIENT_SECRET:QISVXASEFWCY1RSEOLCLMLIC33VDEK3TRKKRAD2H2SQPK4OU


In [22]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

## Data Exploration

The goal here is to plot both Neighborhoods and Venues at the same map to check the density of venues in the city area.

In [23]:
toronto_venues = getNearbyVenues(names=neighborhoods['Neighborhood'], latitudes=neighborhoods['Latitude'], longitudes=neighborhoods['Longitude'])

The Beaches
The Danforth West, Riverdale
India Bazaar, The Beaches West
Studio District
Lawrence Park
Davisville North
North Toronto West, Lawrence Park
Davisville
Moore Park, Summerhill East
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
Rosedale
St. James Town, Cabbagetown
Church and Wellesley
Regent Park, Harbourfront
Garden District, Ryerson
St. James Town
Berczy Park
Central Bay Street
Richmond, Adelaide, King
Harbourfront East, Union Station, Toronto Islands
Toronto Dominion Centre, Design Exchange
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North & West, Forest Hill Road Park
The Annex, North Midtown, Yorkville
University of Toronto, Harbord
Kensington Market, Chinatown, Grange Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Stn A PO Boxes
First Canadian Place, Underground city
Christie
Dufferin, Dovercourt Village
Little Portugal, Trinity
Brockton, Parkdale Village, Exhibition Place
High 

In [24]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  \
0                   The Beaches              43.676357   
1                   The Beaches              43.676357   
2                   The Beaches              43.676357   
3                   The Beaches              43.676357   
4  The Danforth West, Riverdale              43.679557   

   Neighborhood Longitude                               Venue  Venue Latitude  \
0              -79.293031                   Glen Manor Ravine       43.676821   
1              -79.293031  The Big Carrot Natural Food Market       43.678879   
2              -79.293031                 Grover Pub and Grub       43.679181   
3              -79.293031                       Upper Beaches       43.680563   
4              -79.352188                            Pantheon       43.677621   

   Venue Longitude     Venue Category  
0       -79.293942              Trail  
1       -79.297734  Health Food Store  
2       -79.297215                Pub  
3       -79.292869       Neighborhood  
4       -79.351434   Greek Restaurant

In [25]:
toronto_coordinates = address_to_coordinates()
toronto_map_with_venues = map_creator(toronto_venues, latitude=toronto_coordinates[0], longitude=toronto_coordinates[1])

The geograpical coordinate of Toronto City are 43.6534817, -79.3839347.


In [26]:
toronto_map_with_venues

## Data Analysis

One Hot Encoding to be able to count the frequency of each venue.

In [27]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                         Berczy Park     0.000000   
1        Brockton, Parkdale Village, Exhibition Place     0.000000   
2   Business reply mail Processing Centre, South C...     0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
4                                  Central Bay Street     0.014706   
5                                            Christie     0.000000   
6                                Church and Wellesley     0.026667   
7                      Commerce Court, Victoria Hotel     0.000000   
8                                          Davisville     0.000000   
9                                    Davisville North     0.000000   
10                       Dufferin, Dovercourt Village     0.000000   
11             First Canadian Place, Underground city     0.000000   
12    Forest Hill North & West, Forest Hill Road Park     0.000000   
13                           Garden District, Ryerson     0.000000   
14  Harbourfront East, Union Station, Toronto Islands     0.000000   
15                      High Park, The Junction South     0.000000   
16                     India Bazaar, The Beaches West     0.000000   
17          Kensington Market, Chinatown, Grange Park     0.000000   
18                                      Lawrence Park     0.000000   
19                           Little Portugal, Trinity     0.022222   
20                        Moore Park, Summerhill East     0.000000   
21                  North Toronto West, Lawrence Park     0.055556   
22                             Parkdale, Roncesvalles     0.000000   
23        Queen's Park, Ontario Provincial Government     0.030303   
24                          Regent Park, Harbourfront     0.022727   
25                           Richmond, Adelaide, King     0.000000   
26                                           Rosedale     0.000000   
27                                           Roselawn     0.000000   
28                                 Runnymede, Swansea     0.030303   
29                                     St. James Town     0.000000   
30                        St. James Town, Cabbagetown     0.000000   
31                                     Stn A PO Boxes     0.010417   
32                                    Studio District     0.027027   
33  Summerhill West, Rathnelly, South Hill, Forest...     0.000000   
34                The Annex, North Midtown, Yorkville     0.000000   
35                                        The Beaches     0.000000   
36                       The Danforth West, Riverdale     0.023256   
37           Toronto Dominion Centre, Design Exchange     0.000000   
38                     University of Toronto, Harbord     0.029412   

    Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0            0.000000   0.0000              0.0000        0.0000   
1            0.000000   0.0000              0.0000        0.0000   
2            0.000000   0.0000              0.0000        0.0000   
3            0.000000   0.0625              0.0625        0.0625   
4            0.000000   0.0000              0.0000        0.0000   
5            0.000000   0.0000              0.0000        0.0000   
6            0.013333   0.0000              0.0000        0.0000   
7            0.000000   0.0000              0.0000        0.0000   
8            0.000000   0.0000              0.0000        0.0000   
9            0.000000   0.0000              0.0000        0.0000   
10           0.000000   0.0000              0.0000        0.0000   
11           0.000000   0.0000              0.0000        0.0000   
12           0.000000   0.0000              0.0000        0.0000   
13           0.000000   0.0000              0.0000        0.0000   
14           0.000000   0.0000              0.0000        0.0000   
15           0.000000   0.0000              0.0000        0.0000   
16           0.000000   0.0000              0.0000        0.0000   
17           0.0

Now we can list the most frequent venues per neighborhood.

In [28]:
toronto_grouped.shape

(39, 235)

In [29]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Berczy Park----
                venue  freq
0         Coffee Shop  0.09
1  Seafood Restaurant  0.04
2            Beer Bar  0.04
3         Cheese Shop  0.04
4          Restaurant  0.04


----Brockton, Parkdale Village, Exhibition Place----
            venue  freq
0            Café  0.13
1       Nightclub  0.09
2     Coffee Shop  0.09
3  Breakfast Spot  0.09
4   Grocery Store  0.04


----Business reply mail Processing Centre, South Central Letter Processing Plant Toronto----
                  venue  freq
0            Skate Park  0.06
1         Auto Workshop  0.06
2        Farmers Market  0.06
3  Fast Food Restaurant  0.06
4         Burrito Place  0.06


----CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport----
             venue  freq
0   Airport Lounge  0.12
1  Airport Service  0.12
2         Boutique  0.06
3            Plane  0.06
4    Boat or Ferry  0.06


----Central Bay Street----
                venue  freq
0         Coff

In [30]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [31]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Berczy Park           Coffee Shop   
1       Brockton, Parkdale Village, Exhibition Place                  Café   
2  Business reply mail Processing Centre, South C...         Auto Workshop   
3  CN Tower, King and Spadina, Railway Lands, Har...        Airport Lounge   
4                                 Central Bay Street           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0          Cocktail Bar                Bakery    Seafood Restaurant   
1           Coffee Shop        Breakfast Spot             Nightclub   
2                  Park  Fast Food Restaurant    Light Rail Station   
3       Airport Service           Coffee Shop       Harbor / Marina   
4                  Café        Sandwich Place    Italian Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0         Farmers Market           Cheese Shop              Beer Bar   
1  Performing Arts Venue     Convenience Store                   Bar   
2         Farmers Market      Recording Studio         Burrito Place   
3                  Plane   Rental Car Location      Sculpture Garden   
4            Salad Place      Department Store       Thai Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0            Restaurant      Greek Restaurant                    Pub  
1                Bakery    Italian Restaurant                Stadium  
2           Pizza Place            Restaurant                Butcher  
3              Boutique                   Bar          Boat or Ferry  
4   Japanese Restaurant          Burger Joint        Bubble Tea Shop

## Clustering

We can cluster the most common venues types to check for new insights.

In [32]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0])

In [33]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = neighborhoods

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Postal Code   Latitude  Longitude          Borough  \
0         M4E  43.676357 -79.293031     East Toronto   
1         M4K  43.679557 -79.352188     East Toronto   
2         M4L  43.668999 -79.315572     East Toronto   
3         M4M  43.659526 -79.340923     East Toronto   
4         M4N  43.728020 -79.388790  Central Toronto   

                     Neighborhood  Cluster Labels 1st Most Common Venue  \
0                     The Beaches               0                   Pub   
1    The Danforth West, Riverdale               0      Greek Restaurant   
2  India Bazaar, The Beaches West               0                  Park   
3                 Studio District               0           Coffee Shop   
4                   Lawrence Park               2                  Park   

  2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
0                 Trail     Health Food Store            Dance Studio   
1           Coffee Shop    Italian Restaurant  Furniture / Home Store   
2            Steakhouse        Ice Cream Shop       Fish & Chips Shop   
3   American Restaurant                Bakery                 Brewery   
4              Bus Line           Swim School                Wine Bar   

         5th Most Common Venue        6th Most Common Venue  \
0  Eastern European Restaurant          Dumpling Restaurant   
1                    Bookstore               Ice Cream Shop   
2                          Pub               Sandwich Place   
3                         Café                    Gastropub   
4                Deli / Bodega  Eastern European Restaurant   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0            Donut Shop      Doner Restaurant               Dog Run   
1            Restaurant           Pizza Place                Lounge   
2         Burrito Place      Sushi Restaurant           Pizza Place   
3              Wine Bar           Fish Market                  Park   
4   Dumpling Restaurant            Donut Shop      Doner Restaurant   

      10th Most Common Venue  
0        Distribution Center  
1               Liquor Store  
2               Liquor Store  
3  Middle Eastern Restaurant  
4                    Dog Run

In [34]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Cluster Analysis

### Cluster 1

In [35]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Latitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0   43.676357               0                   Pub                 Trail   
1   43.679557               0      Greek Restaurant           Coffee Shop   
2   43.668999               0                  Park            Steakhouse   
3   43.659526               0           Coffee Shop   American Restaurant   
5   43.712751               0          Dance Studio                 Hotel   
6   43.715383               0           Coffee Shop        Clothing Store   
7   43.704324               0           Pizza Place          Dessert Shop   
9   43.686412               0           Coffee Shop          Liquor Store   
11  43.667967               0           Coffee Shop            Restaurant   
12  43.665860               0           Coffee Shop               Gay Bar   
13  43.654260               0           Coffee Shop                   Pub   
14  43.657162               0        Clothing Store           Coffee Shop   
15  43.651494               0           Coffee Shop                  Café   
16  43.644771               0           Coffee Shop          Cocktail Bar   
17  43.657952               0           Coffee Shop                  Café   
18  43.650571               0           Coffee Shop                  Café   
19  43.640816               0           Coffee Shop              Aquarium   
20  43.647177               0           Coffee Shop                 Hotel   
21  43.648198               0           Coffee Shop            Restaurant   
24  43.672710               0        Sandwich Place                  Café   
25  43.662696               0                  Café             Bookstore   
26  43.653206               0           Coffee Shop    Mexican Restaurant   
27  43.628947               0        Airport Lounge       Airport Service   
28  43.646435               0           Coffee Shop    Italian Restaurant   
29  43.648429               0           Coffee Shop                  Café   
30  43.669542               0         Grocery Store                  Café   
31  43.669005               0              Pharmacy                Bakery   
32  43.647927               0                   Bar           Coffee Shop   
33  43.636847               0                  Café           Coffee Shop   
34  43.661608               0    Mexican Restaurant       Thai Restaurant   
35  43.648960               0             Gift Shop        Breakfast Spot   
36  43.651571               0           Coffee Shop                  Café   
37  43.662301               0           Coffee Shop           Yoga Studio   
38  43.662744               0         Auto Workshop                  Park   

            3rd Most Common Venue        4th Most Common Venue  \
0               Health Food Store                 Dance Studio   
1              Italian Restaurant       Furniture / Home Store   
2                  Ice Cream Shop            Fish & Chips Shop   
3                          Bakery                      Brewery   
5                            Park         Gym / Fitness Center   
6                     Yoga Studio           Mexican Restaurant   
7                  Sandwich Place                          Gym   
9             Fried Chicken Joint                         Bank   
11                           Café                  Pizza Place   
12               Sushi Restaurant          Japanese Restaurant   
13                           Park                       Bakery   
14                           Café          Japanese Restaurant   
15                   Cocktail Bar                   Restaurant   
16                         Bakery           Seafood Restaurant   
17                 Sandwich Place           Italian Restaurant   
18                            Gym                   Restaurant   
19                          Hotel                         Café   
20                     Restaurant                         Café   
21                           Café                      

### Cluster 2

In [36]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Latitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
8  43.689574               1                 Trail            Playground   

  3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
8              Wine Bar          Dance Studio  Eastern European Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8   Dumpling Restaurant            Donut Shop      Doner Restaurant   

  9th Most Common Venue 10th Most Common Venue  
8               Dog Run    Distribution Center

### Cluster 3

In [37]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Latitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
4  43.72802               2                  Park              Bus Line   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
4           Swim School              Wine Bar         Deli / Bodega   

         6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
4  Eastern European Restaurant   Dumpling Restaurant            Donut Shop   

  9th Most Common Venue 10th Most Common Venue  
4      Doner Restaurant                Dog Run

### Cluster 4

In [38]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Latitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
10  43.679563               3                  Park                 Trail   
23  43.696948               3      Sushi Restaurant                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
10            Playground              Wine Bar          Dance Studio   
23         Jewelry Store                 Trail              Wine Bar   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
10   Dumpling Restaurant            Donut Shop      Doner Restaurant   
23   Distribution Center          Dessert Shop    Dim Sum Restaurant   

   9th Most Common Venue 10th Most Common Venue  
10               Dog Run    Distribution Center  
23                 Diner         Discount Store

### Cluster 5

In [39]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Latitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
22  43.711695               4           Music Venue                Garden   

   3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
22              Wine Bar         Deli / Bodega  Eastern European Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
22   Dumpling Restaurant            Donut Shop      Doner Restaurant   

   9th Most Common Venue 10th Most Common Venue  
22               Dog Run    Distribution Center

We can observe, based on the 5-means Clustering, that the Cluster no. 1 has a lot of Coffee Shops and breakfest related venues and occupies a large area of the city.

A person interested in opening a new business in Toronto City could use this information to help decide if it is worth or not.